In [9]:
!pip install transformers

In [13]:
!pip install peft

In [2]:
# from transformers import AutoModelForSeq2SeqLM
# from peft import get_peft_config, get_peft_model, LoraConfig, TaskType
# import torch
# model_name_or_path = "microsoft/GODEL-v1_1-large-seq2seq"
# tokenizer_name_or_path = "microsoft/GODEL-v1_1-large-seq2seq"

In [2]:
from transformers import AutoModelForSeq2SeqLM, AutoTokenizer

# Replace 'microsoft/GODEL-v1_1-large-seq2seq' with the model name
model_name = 'microsoft/GODEL-v1_1-large-seq2seq'

# Load the model and tokenizer
model = AutoModelForSeq2SeqLM.from_pretrained(model_name)
tokenizer = AutoTokenizer.from_pretrained(model_name)

In [15]:
# Output directory
output_dir = "medbot_model"

# Save the model and tokenizer using the standard Hugging Face naming convention
model.save_pretrained(output_dir)
tokenizer.save_pretrained(output_dir)

('medbot_model/tokenizer_config.json',
 'medbot_model/special_tokens_map.json',
 'medbot_model/tokenizer.json')

In [12]:
# # peft config

# peft_config = LoraConfig(
#     task_type=TaskType.SEQ_2_SEQ_LM, inference_mode=False, r=6, lora_alpha=16, lora_dropout=0.2
# )

In [14]:
# model = get_peft_model(model, peft_config)
# model.print_trainable_parameters()

# output_dir = "medbot_model_peft"

# model.save_pretrained(output_dir)
# tokenizer.save_pretrained(output_dir)

trainable params: 1,769,472 || all params: 739,410,944 || trainable%: 0.23930833244469804


('medbot_model_peft/tokenizer_config.json',
 'medbot_model_peft/special_tokens_map.json',
 'medbot_model_peft/tokenizer.json')

In [8]:
# ============================== Load Dataset ==========================

In [3]:
import pandas as pd

df = pd.read_csv('/content/drive/MyDrive/Dataset/diseaseDataSetFull2.csv')
df

disease  \
0                            Fungal infection   
1                            Fungal infection   
2                            Fungal infection   
3                            Fungal infection   
4                            Fungal infection   
...                                       ...   
4915  (vertigo) Paroymsal  Positional Vertigo   
4916                                     Acne   
4917                  Urinary tract infection   
4918                                Psoriasis   
4919                                 Impetigo   

                                               symptoms  \
0     itching,skin_rash,nodal_skin_eruptions,dischro...   
1     skin_rash,nodal_skin_eruptions,dischromic__pat...   
2      itching,nodal_skin_eruptions,dischromic__patches   
3                 itching,skin_rash,dischromic__patches   
4                itching,skin_rash,nodal_skin_eruptions   
...                                                 ...   
4915  vomiting,headache,nausea,spinning_movements,lo...   
4916   skin_rash,pus_filled_pimples,blackheads,scurring   
4917  burning_micturition,bladder_discomfort,foul_sm...   
4918  skin_rash,joint_pain,skin_peeling,silver_like_...   
4919  skin_rash,high_fever,blister,red_sore_around_n...   

                                            precautions  
0     bath twice, use detol or neem in bathing water...  
1     bath twice, use detol or neem in bathing water...  
2     bath twice, use detol or neem in bathing water...  
3     bath twice, use detol or neem in bathing water...  
4     bath twice, use detol or neem in bathing water...  
...                                                 ...  
4915  lie down, avoid sudden change in body, avoid a...  
4916  bath twice, avoid fatty spicy food, drink plen...  
4917  drink plenty of water, increase vitamin c inta...  
4918  wash hands with warm soapy water, stop bleedin...  
4919  soak affected area in warm water, use antibiot...  

[4920 rows x 3 columns]

In [4]:
def dataframe_to_dataset(df):
    """
    Convert a DataFrame with columns 'disease', 'symptoms', and 'precautions'
    into a list of tuples dataset.

    Parameters:
        df (pd.DataFrame): Input DataFrame with columns 'disease', 'symptoms', and 'precautions'.

    Returns:
        list: A list of tuples, where each tuple contains information about a specific disease,
              symptoms, and precautions.
    """
    if not all(col in df.columns for col in ['disease', 'symptoms', 'precautions']):
        raise ValueError("DataFrame must contain 'disease', 'symptoms', and 'precautions' columns.")

    dataset = []
    for _, row in df.iterrows():
        disease = row['disease']
        symptoms = row['symptoms']
        precautions = row['precautions']
        dataset.append((disease, symptoms, precautions))

    return dataset

data = dataframe_to_dataset(df)
data[:10]

[('Fungal infection',
  'itching,skin_rash,nodal_skin_eruptions,dischromic__patches',
  'bath twice, use detol or neem in bathing water, keep infected area dry, use clean cloths'),
 ('Fungal infection',
  'skin_rash,nodal_skin_eruptions,dischromic__patches',
  'bath twice, use detol or neem in bathing water, keep infected area dry, use clean cloths'),
 ('Fungal infection',
  'itching,nodal_skin_eruptions,dischromic__patches',
  'bath twice, use detol or neem in bathing water, keep infected area dry, use clean cloths'),
 ('Fungal infection',
  'itching,skin_rash,dischromic__patches',
  'bath twice, use detol or neem in bathing water, keep infected area dry, use clean cloths'),
 ('Fungal infection',
  'itching,skin_rash,nodal_skin_eruptions',
  'bath twice, use detol or neem in bathing water, keep infected area dry, use clean cloths'),
 ('Fungal infection',
  'skin_rash,nodal_skin_eruptions,dischromic__patches',
  'bath twice, use detol or neem in bathing water, keep infected area dry, u

In [5]:
data[:10]

[('Fungal infection',
  'itching,skin_rash,nodal_skin_eruptions,dischromic__patches',
  'bath twice, use detol or neem in bathing water, keep infected area dry, use clean cloths'),
 ('Fungal infection',
  'skin_rash,nodal_skin_eruptions,dischromic__patches',
  'bath twice, use detol or neem in bathing water, keep infected area dry, use clean cloths'),
 ('Fungal infection',
  'itching,nodal_skin_eruptions,dischromic__patches',
  'bath twice, use detol or neem in bathing water, keep infected area dry, use clean cloths'),
 ('Fungal infection',
  'itching,skin_rash,dischromic__patches',
  'bath twice, use detol or neem in bathing water, keep infected area dry, use clean cloths'),
 ('Fungal infection',
  'itching,skin_rash,nodal_skin_eruptions',
  'bath twice, use detol or neem in bathing water, keep infected area dry, use clean cloths'),
 ('Fungal infection',
  'skin_rash,nodal_skin_eruptions,dischromic__patches',
  'bath twice, use detol or neem in bathing water, keep infected area dry, u

In [7]:
# =============================== Training  =====================================

In [6]:
from transformers import AutoTokenizer, AutoModelForSeq2SeqLM, AdamW
from torch.utils.data import Dataset, DataLoader
import torch

device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
model = model.to(device)

# Sample Data
sample_data = data

class CustomDataset(Dataset):
    def __init__(self, data, tokenizer, max_length):
        self.data = data
        self.tokenizer = tokenizer
        self.max_length = max_length

    def __len__(self):
        return len(self.data)

    def __getitem__(self, index):
        disease, symptoms, precautions = self.data[index]
        source_text = f"I am feeling {symptoms}"
        target_text = f"You might have {disease}, the precautions are {precautions}"

        # Tokenize the source and target texts separately
        source_tokens = self.tokenizer(source_text, padding="max_length", max_length=self.max_length, return_tensors="pt")
        target_tokens = self.tokenizer(target_text, padding="max_length", max_length=self.max_length, return_tensors="pt")

        # Prepare the inputs and labels for the Seq2Seq model
        input_ids = source_tokens.input_ids.squeeze()
        attention_mask = source_tokens.attention_mask.squeeze()
        labels = target_tokens.input_ids.squeeze()

        return {
            "input_ids": input_ids,
            "attention_mask": attention_mask,
            "labels": labels,
        }

def fine_tune_and_save_model(model, tokenizer):
    # Load tokenizer and create dataset
    # checkpoint = "microsoft/GODEL-v1_1-large-seq2seq"
    # tokenizer = AutoTokenizer.from_pretrained(checkpoint)
    max_length = 128  # You can adjust this based on your input sequence length requirements
    dataset = CustomDataset(sample_data, tokenizer, max_length)

    # Data loader
    batch_size = 2
    dataloader = DataLoader(dataset, batch_size=batch_size, shuffle=True)

    # Load the model
    # from the parameter

    # Hyperparameters
    learning_rate = 2e-5
    num_epochs = 2
    num_warmup_steps = 100

    optimizer = AdamW(model.parameters(), lr=learning_rate)

    # Training loop
    model.train()
    for epoch in range(num_epochs):
        total_loss = 0.0
        for batch in dataloader:
            optimizer.zero_grad()

            input_ids = batch["input_ids"]
            attention_mask = batch["attention_mask"]
            labels = batch["labels"]

            input_ids = batch["input_ids"].to(device)
            attention_mask = batch["attention_mask"].to(device)
            labels = batch["labels"].to(device)


            outputs = model(input_ids=input_ids, attention_mask=attention_mask, labels=labels)
            loss = outputs.loss
            total_loss += loss.item()

            loss.backward()
            optimizer.step()

        average_loss = total_loss / len(dataloader)
        print(f"Epoch {epoch+1}/{num_epochs} - Average Loss: {average_loss:.4f}")

    # Save the fine-tuned model and tokenizer
    output_dir = "medbot_model_epoch3_s512"
    model.save_pretrained(output_dir)
    tokenizer.save_pretrained(output_dir)

In [7]:
fine_tune_and_save_model(model, tokenizer)

/usr/local/lib/python3.10/dist-packages/transformers/optimization.py:306: FutureWarning: This implementation of AdamW is deprecated and will be removed in a future version. Use the PyTorch implementation torch.optim.AdamW instead, or set `no_deprecation_warning=True` to disable this warning
  warnings.warn(


Epoch 1/2 - Average Loss: 0.1588
Epoch 2/2 - Average Loss: 0.0038
